 Project Structure

    tools.py – Provides auxiliary tools for the agent.
    retriever.py – Implements retrieval functions to support knowledge access.
    app.py – Integrates all components into a fully functional agent, which we’ll finalize in the last part of this unit.

### Building the Guestbook Tool

Step 1: Load and Prepare the Dataset

In [7]:
from llama_index.core.schema import Document
import pandas as pd
#from huggingface_hub import hf_hub_download

In [8]:
# Load the dataset
#guest_dataset = datasets.load_dataset("agents-course/unit3-invitees", split="train")
guest_dataset = pd.read_parquet("/home/cairo/code/alfred-agent-rag/data/train-00000-of-00001.parquet")

# Convert dataset entries into Document objects
docs = [
    Document(
        text="\n".join([
            f"Name: {guest_dataset['name'][i]}",
            f"Relation: {guest_dataset['relation'][i]}",
            f"Description: {guest_dataset['description'][i]}",
            f"Email: {guest_dataset['email'][i]}"
        ]),
        metadata={"name": guest_dataset['name'][i]}
    )
    for i in range(len(guest_dataset))
]

In [9]:
guest_dataset

name                         relation  \
0      Ada Lovelace                      best friend   
1  Dr. Nikola Tesla  old friend from university days   
2       Marie Curie                      no relation   

                                         description                     email  
0  Lady Ada Lovelace is my best friend. She is an...  ada.lovelace@example.com  
1  Dr. Nikola Tesla is an old friend from your un...    nikola.tesla@gmail.com  
2  Marie Curie was a groundbreaking physicist and...   marie.curie@example.com

Step 2: Create the Retriever Tool

Now, let’s create a custom tool that Alfred can use to search through our guest information.

In [11]:
from llama_index.core.tools import FunctionTool
from llama_index.retrievers.bm25 import BM25Retriever

bm25_retriever = BM25Retriever.from_defaults(nodes=docs)

def get_guest_info_retriever(query: str) -> str:
    """Retrieves detailed information about gala guests based on their name or relation."""
    results = bm25_retriever.retrieve(query)
    if results:
        return "\n\n".join([doc.text for doc in results[:3]])
    else:
        return "No matching guest information found."

# Initialize the tool
guest_info_tool = FunctionTool.from_defaults(get_guest_info_retriever)

Let’s understand this tool step-by-step.

- The docstring helps the agent understand when and how to use this tool
- The type decorators define what parameters the tool expects (in this case, a search query)
- We’re using a BM25Retriever, which is a powerful text retrieval algorithm that doesn’t require embeddings
- The method processes the query and returns the most relevant guest information

Step 3: Integrate the Tool with Alfred

In [14]:
from huggingface_hub import login

login()

In [15]:
from llama_index.core.agent.workflow import AgentWorkflow
from llama_index.llms.huggingface_api import HuggingFaceInferenceAPI

# Initialize the Hugging Face model
llm = HuggingFaceInferenceAPI(model_name="Qwen/Qwen2.5-Coder-32B-Instruct")

# Create Alfred, our gala agent, with the guest info tool
alfred = AgentWorkflow.from_tools_or_functions(
    [guest_info_tool],
    llm=llm,
)

# Example query Alfred might receive during the gala
response = await alfred.run("Tell me about our guest named 'Lady Ada Lovelace'.")

print("🎩 Alfred's Response:")
print(response)

Exception in callback Dispatcher.span.<locals>.wrapper.<locals>.handle_future_result(span_id='Workflow.run...-e3cd19dfc9c6', bound_args=<BoundArgumen...mory': None})>, instance=<llama_index....x76ae1634edb0>, context=<_contextvars...x76ae168519c0>)(<WorkflowHand...ompletions'")>) at /home/cairo/anaconda3/lib/python3.12/site-packages/llama_index/core/instrumentation/dispatcher.py:274
handle: <Handle Dispatcher.span.<locals>.wrapper.<locals>.handle_future_result(span_id='Workflow.run...-e3cd19dfc9c6', bound_args=<BoundArgumen...mory': None})>, instance=<llama_index....x76ae1634edb0>, context=<_contextvars...x76ae168519c0>)(<WorkflowHand...ompletions'")>) at /home/cairo/anaconda3/lib/python3.12/site-packages/llama_index/core/instrumentation/dispatcher.py:274>
Traceback (most recent call last):
  File "/home/cairo/anaconda3/lib/python3.12/site-packages/llama_index/core/workflow/context.py", line 583, in _step_worker
    new_ev = await instrumented_step(**kwargs)
             ^^^^^^^^^^^^^^

WorkflowRuntimeError: Error in step 'run_agent_step': 402, message='Payment Required', url='https://router.huggingface.co/hf-inference/models/Qwen/Qwen2.5-Coder-32B-Instruct/v1/chat/completions'

What’s happening in this final step:

- We initialize a Hugging Face model using the HuggingFaceInferenceAPI class
- We create our agent (Alfred) as a AgentWorkflow, including the tool we just created
- We ask Alfred to retrieve information about a guest named “Lady Ada Lovelace”

### Building and Integrating Tools for Your Agent

Give Your Agent Access to the Web

In [18]:
from llama_index.tools.duckduckgo import DuckDuckGoSearchToolSpec
from llama_index.core.tools import FunctionTool

# Initialize the DuckDuckGo search tool
tool_spec = DuckDuckGoSearchToolSpec()

search_tool = FunctionTool.from_defaults(tool_spec.duckduckgo_full_search)
# Example usage
response = search_tool("Who's the current President of Brazil?")
print(response.raw_output[-1]['body'])

He served two terms as the president of Brazil from 2003 to 2010 and left office with an approval rating of 80%. Brazilian president-elect for the leftist Workers Party (PT) Luiz Inacio Lula da ...


Creating a Custom Tool for Weather Information to Schedule the Fireworks

In [19]:
import random
from llama_index.core.tools import FunctionTool

def get_weather_info(location: str) -> str:
    """Fetches dummy weather information for a given location."""
    # Dummy weather data
    weather_conditions = [
        {"condition": "Rainy", "temp_c": 15},
        {"condition": "Clear", "temp_c": 25},
        {"condition": "Windy", "temp_c": 20}
    ]
    # Randomly select a weather condition
    data = random.choice(weather_conditions)
    return f"Weather in {location}: {data['condition']}, {data['temp_c']}°C"

# Initialize the tool
weather_info_tool = FunctionTool.from_defaults(get_weather_info)

Creating a Hub Stats Tool for Influential AI Builders

In [20]:
import random
from llama_index.core.tools import FunctionTool
from huggingface_hub import list_models

def get_hub_stats(author: str) -> str:
    """Fetches the most downloaded model from a specific author on the Hugging Face Hub."""
    try:
        # List models from the specified author, sorted by downloads
        models = list(list_models(author=author, sort="downloads", direction=-1, limit=1))

        if models:
            model = models[0]
            return f"The most downloaded model by {author} is {model.id} with {model.downloads:,} downloads."
        else:
            return f"No models found for author {author}."
    except Exception as e:
        return f"Error fetching models for {author}: {str(e)}"

# Initialize the tool
hub_stats_tool = FunctionTool.from_defaults(get_hub_stats)

# Example usage
print(hub_stats_tool("facebook")) # Example: Get the most downloaded model by Facebook

The most downloaded model by facebook is facebook/esmfold_v1 with 24,213,202 downloads.


Integrating Tools with Alfred

In [21]:
from llama_index.core.agent.workflow import AgentWorkflow
from llama_index.llms.huggingface_api import HuggingFaceInferenceAPI

# Initialize the Hugging Face model
llm = HuggingFaceInferenceAPI(model_name="Qwen/Qwen2.5-Coder-32B-Instruct")
# Create Alfred with all the tools
alfred = AgentWorkflow.from_tools_or_functions(
    [search_tool, weather_info_tool, hub_stats_tool],
    llm=llm
)

# Example query Alfred might receive during the gala
response = await alfred.run("What is Facebook and what's their most popular model?")

print("🎩 Alfred's Response:")
print(response)

Exception in callback Dispatcher.span.<locals>.wrapper.<locals>.handle_future_result(span_id='Workflow.run...-55bd0ee16e6f', bound_args=<BoundArgumen...mory': None})>, instance=<llama_index....x76ae0f7cddf0>, context=<_contextvars...x76ae50734e40>)(<WorkflowHand...ompletions'")>) at /home/cairo/anaconda3/lib/python3.12/site-packages/llama_index/core/instrumentation/dispatcher.py:274
handle: <Handle Dispatcher.span.<locals>.wrapper.<locals>.handle_future_result(span_id='Workflow.run...-55bd0ee16e6f', bound_args=<BoundArgumen...mory': None})>, instance=<llama_index....x76ae0f7cddf0>, context=<_contextvars...x76ae50734e40>)(<WorkflowHand...ompletions'")>) at /home/cairo/anaconda3/lib/python3.12/site-packages/llama_index/core/instrumentation/dispatcher.py:274>
Traceback (most recent call last):
  File "/home/cairo/anaconda3/lib/python3.12/site-packages/llama_index/core/workflow/context.py", line 583, in _step_worker
    new_ev = await instrumented_step(**kwargs)
             ^^^^^^^^^^^^^^

WorkflowRuntimeError: Error in step 'run_agent_step': 402, message='Payment Required', url='https://router.huggingface.co/hf-inference/models/Qwen/Qwen2.5-Coder-32B-Instruct/v1/chat/completions'

Conclusion

By integrating these tools, Alfred is now equipped to handle a variety of tasks, from web searches to weather updates and model statistics. This ensures he remains the most informed and engaging host at the gala.

### Creating Your Gala Agent

https://huggingface.co/learn/agents-course/unit3/agentic-rag/agent?agents-frameworks=llama-index